如果刚打开，请先打开一个[登录链接](https://mysunlife.sunlife.com.hk/SunOffice/),然后点一下登入

In [1]:
#运行下方代码，自动打开浏览器并登录，登录后请选择你要的课程，点击启动后再运行后面代码
from selenium import webdriver
import time,re
import datetime
from selenium.webdriver.common.action_chains import ActionChains
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC

def has(a_list):
    '''判断一个list是否为空，返回True/False'''
    if len(a_list)==0:
        return False
    else:
        return True

class Answers():
    '''一次测验某一页的答案'''
    def __init__(self):
        '''{'ans_str':False/True/None}'''
        #初始化所有选项为None
        self.answers={}
        choices=self.get_choice()
        for ans_str, _ in choices.items():
            self.answers[ans_str]=None

    def get_choice(self):
        '''返回带有文字对应input_element的字典'''
        # 定位所有 class 为 "choice-view" 的 div 元素
        choice_views = driver.find_elements_by_class_name('choice-view')
        
        # 创建一个空字典来保存文本和对应的 input 元素
        choices = {}
        
        # 遍历所有 "choice-view" 元素
        for choice_view in choice_views:
            # 在每个 "choice-view" 元素中，定位 class 为 "choice-view__rich-text-view" 的 div 元素
            rich_text_view = choice_view.find_element_by_class_name('choice-view__rich-text-view')
            # 获取这个 div 元素的文本
            text = rich_text_view.text
            # 在这个 "choice-view" 元素中，定位 class 为 "choice-view__mock-active-element" 的 input 元素
            input_element = choice_view.find_element_by_class_name('choice-view__mock-active-element')
            # 将文本和对应的 input 元素保存在字典中
            choices[text] = input_element
        
        # 输出字典
        # for text, input_element in choices.items():
        #     print('Text:', text)
        #     print('Input element:', input_element)
        self.cur_choices=choices
        return choices
    
    def select_one_choice(self):
        '''选择一个可选择的ans_str'''
        for ans_str, info in self.answers.items():
            if info==True:
                self.one_choice=ans_str
                return ans_str
            elif info==None:
                self.one_choice=ans_str
                return ans_str
        print('No answer')
    
    def click_choice(self):
        '''由于限制，得这样点击选项'''
        input_element=self.cur_choices[self.one_choice]
        for i in range(3): #多點幾次
            # 创建一个 ActionChains 对象
            actions = ActionChains(driver)
            
            # 将鼠标移动到 input 元素上
            actions.move_to_element(input_element).pause(1)
            
            # 点击 input 元素
            actions.click(input_element).pause(1)
            
            # 执行 ActionChains 中的所有操作
            actions.perform()

        time.sleep(5)
        #点击提交
        driver.find_element_by_xpath('//button[div[text()="提交"]]').click()
        time.sleep(5)
        result=driver.find_element_by_class_name('quiz-feedback-panel__header').text
        # driver.find_element_by_xpath('//button[div[text()="繼續"]]').click()
        if result=="錯誤":
            return self.update_answer(self.one_choice, False)
        else:
            return self.update_answer(self.one_choice, True)

    def update_answer(self, ans_str, result):
        if result==True: #更新并把其他选项列为False
            for ans_stri in self.answers.keys():
                if ans_stri==ans_str:
                    self.answers[ans_stri]=True
                else:
                    self.answers[ans_stri]=False
        elif result==False: #更新一个选项就可以了
            self.answers[ans_str]=False

def click_next():
    '''这是一个通用的click，点击quiz-control-panel__button的最后一个按钮'''
    buttons = driver.find_elements_by_xpath('//div[contains(@class, "quiz-control-panel__container_right")]//button[contains(@class, "quiz-control-panel__button") and not(contains(@style, "display: none;"))]')
    if buttons:
        buttons[-1].click()

def go_test():
    '''这个函数要完成测试'''
    all_answers={}
    finish=False
    while not finish:
        #1.点击按钮开始测试
        if has(driver.find_elements_by_xpath('//button[div[contains(text(), "開始")] and not(contains(@style, "display: none;"))]')):
            driver.find_element_by_xpath('//button[div[contains(text(), "開始")] and not(contains(@style, "display: none;"))]').click()
        elif has(driver.find_elements_by_xpath('//*[text()="重試評估" and not(contains(@style, "display: none;"))]')):
            driver.find_element_by_xpath('//*[text()="重試評估"]').click()
        elif has(driver.find_elements_by_xpath('//*[text()="開始測驗" and not(contains(@style, "display: none;"))]')):
            driver.find_element_by_xpath('//*[text()="開始測驗"]').click()
        else:
            print('Unknown page, maybe pass')
            break
        time.sleep(5)

        #2.进入试题界面了
        text_temp=driver.find_element_by_class_name('quiz-top-panel__question-score-info').text #例如：問題 1/3
        parts = text_temp.split(' ')[1].split('/')
        current_question = int(parts[0])  # 当前问题序号
        total_questions = int(parts[1])  # 问题总数
        
        for i in range(total_questions):
            text_temp=driver.find_element_by_class_name('quiz-top-panel__question-score-info').text #例如：問題 1/3
            parts = text_temp.split(' ')[1].split('/')
            current_question = int(parts[0])  # 当前问题序号
        
            #如果第一次见到选项，则初始化
            if current_question not in all_answers.keys():
                all_answers[current_question]=Answers() #里面会自动根据当前页面更新选项
                
            all_answers[current_question].get_choice()
            all_answers[current_question].select_one_choice()
            all_answers[current_question].click_choice() #会自动得到本题对错并更新答案
            time.sleep(5)

            #点击继续或者检视结果
            click_next()
            # if has(driver.find_elements_by_xpath('//button[div[text()="繼續"] and not(contains(@style, "display: none;"))]')):
            #     driver.find_element_by_xpath('//button[div[text()="繼續"]]').click()
            # elif has(driver.find_elements_by_xpath('//button[div[text()="檢視結果"] and not(contains(@style, "display: none;"))]')):
            #     driver.find_element_by_xpath('//button[div[text()="檢視結果"]]').click()
            time.sleep(2)
            #有下一页的话说明成功了
            if has(driver.find_elements_by_xpath('//button[div[text()="下一頁"] and not(contains(@style, "display: none;"))]')):
                driver.find_element_by_xpath('//button[div[text()="下一頁"] and not(contains(@style, "display: none;"))]').click()
                finish=True
            time.sleep(5)

class button_is_clickable(object):
    def __init__(self, locator):
        self.locator = locator

    def __call__(self, driver):
        button = driver.find_element(*self.locator)
        class_name = button.get_attribute("class")
        if class_name != "cs-button btn cs-disabled":
            return button
        else:
            return False

def parse_cookie_file(cookie_file):
    cookies = []
    with open(cookie_file, 'r') as f:
        for line in f:
            if not re.match(r'^#', line) and line.strip():
                line_fields = line.strip().split('\t')
                if len(line_fields) == 7:
                    cookies.append({
                        'name': line_fields[5],
                        'value': line_fields[6],
                        'domain': line_fields[0],
                        'path': line_fields[2],
                        'expiry': int(line_fields[4]) if line_fields[4] != '0' else None,
                        'secure': False if line_fields[3] == 'FALSE' else True,
                    })
    return cookies
    
#手动登录
driver = webdriver.Firefox(executable_path='/snap/bin/firefox.geckodriver')
driver.get(r'https://mysunlife.sunlife.com.hk/SunOffice/')



wait = WebDriverWait(driver, 30)

sign_in_button = wait.until(
    EC.element_to_be_clickable((By.CSS_SELECTOR, ".yellow-button.line_height_18.sign-button.button.button-md.button-default.button-default-md.button-full.button-full-md"))
)

# 添加cookie刷新
cookies = parse_cookie_file('cookies.txt')

# 添加cookie
for cookie in cookies:
    if 'expiry' in cookie:
        del cookie['expiry']  # Selenium不支持直接设置'expiry'，将其删除
    driver.add_cookie(cookie)

# 刷新页面以应用cookie
driver.refresh()
sign_in_button = wait.until(
    EC.element_to_be_clickable((By.CSS_SELECTOR, ".yellow-button.line_height_18.sign-button.button.button-md.button-default.button-default-md.button-full.button-full-md"))
)
sign_in_button.click()

#等待登录页面
username_input = wait.until(
    EC.visibility_of_element_located((By.ID, "okta-signin-username"))
)
username_input.send_keys("Z0S851")
driver.find_element_by_id("okta-signin-password").send_keys('All131415!')
driver.find_element_by_id('okta-signin-submit').click()


print('Log in by hand')

Log in by hand


# 主程序(选好课程后运行)

In [2]:
# 获取所有窗口的句柄，切换到最后一个
window_handles = driver.window_handles
driver.switch_to.window(window_handles[-1])
driver.switch_to.default_content()
iframe = driver.find_element_by_xpath('//iframe[1]')
driver.switch_to.frame(iframe)
while True:
    #1.是有计时器的情况，则等待翻页
    if has(driver.find_elements_by_css_selector('.progressbar__label.progressbar__label_type_time')):
        # 解析时间字符串
        timer=driver.find_element_by_css_selector('.progressbar__label.progressbar__label_type_time').text
        current_time_string, total_time_string = timer.split(' / ')
        current_time = datetime.datetime.strptime(current_time_string, '%M:%S')
        total_time = datetime.datetime.strptime(total_time_string, '%M:%S')
        
        # 判断是否已经达到总时间
        if current_time >= total_time:
            # 找到按钮并点击下一页
            driver.find_element_by_xpath('//button[@aria-label="next slide"]').click()
            print(datetime.datetime.now())
        else:
            # 计算两个时间相差的秒数
            seconds = int((total_time-current_time).total_seconds())+5
            print('Wait', seconds)
            time.sleep(seconds)
    #2.有“开始评估“按钮，则点击进入测评
    elif has(driver.find_elements_by_xpath('//button[div[contains(text(), "開始")] and not(contains(@style, "display: none;"))]')):
        print("开始做题，如果中途暂停，请手动回到开始评估页面（不用点击），然后重新运行这里的程序")
        go_test()
        

    #3.有“重新评估“按钮，则点击进入测评
    elif has(driver.find_elements_by_xpath('//*[text()="重試評估" and not(contains(@style, "display: none;"))]')):
        print("开始做题，如果中途暂停，请手动回到开始评估页面（不用点击），然后重新运行这里的程序")
        go_test()

    #4.是没有显示时间的课程
    elif has(driver.find_elements_by_id("seek")):
        next_button = WebDriverWait(driver, 180).until(
            button_is_clickable((By.ID, "next"))
        )
        # 点击按钮
        next_button.click()
        print('Click')

    #5.是要验证码的课程
    elif has(driver.find_elements_by_css_selector("#btn_next_page img.btn-highlight")):
        img = WebDriverWait(driver, 200).until(EC.visibility_of_element_located((By.CSS_SELECTOR, "#btn_next_page img.btn-highlight")))
        img.click()
        print('Click next')

    else:
        print('Unknow page')
        break
        
        

Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next
Click next


TimeoutException: Message: 
